In [ ]:
pip -q install -U langchain huggingface_hub tiktoken PyPDF2 pypdf sentence_transformers together FlagEmbedding faiss-gpu openai text-generation pymupdf

## RetrievalQA with LLaMA 2-70B on Together API

In [ ]:
import os

os.environ["TOGETHER_API_KEY"] = "53b21bdab47f250b23da974391f9c0e7fb07ec242aec6c1e17d329c931edfa38"

In [ ]:
pip install asyncpg

# Setting up Together API


In [ ]:
import together

# set your API key
together.api_key = os.environ["TOGETHER_API_KEY"]

# list available models and descriptons
# models = together.Models.list()

In [ ]:
# together.Models.start("togethercomputer/llama-2-70b-chat")

In [ ]:
import together

import logging
from typing import Any, Dict, List, Mapping, Optional

from pydantic import Extra, Field, root_validator

from langchain.callbacks.manager import CallbackManagerForLLMRun
from langchain.llms.base import LLM
from langchain.llms.utils import enforce_stop_tokens
from langchain.utils import get_from_dict_or_env


from gradio_client import Client

client = Client("https://073695670dbd200693.gradio.live/")

class TogetherLLM(LLM):
    """Together large language models."""

    model: str = "togethercomputer/llama-2-70b-chat"
    """model endpoint to use"""

    together_api_key: str = os.environ["TOGETHER_API_KEY"]
    """Together API key"""

    temperature: float = 0.7
    """What sampling temperature to use."""

    max_tokens: int = 512
    """The maximum number of tokens to generate in the completion."""

    class Config:
        extra = Extra.forbid

    @root_validator()
    def validate_environment(cls, values: Dict) -> Dict:
        """Validate that the API key is set."""
        api_key = get_from_dict_or_env(
            values, "together_api_key", "TOGETHER_API_KEY"
        )
        values["together_api_key"] = api_key
        return values

    @property
    def _llm_type(self) -> str:
        """Return type of LLM."""
        return "together"

    def _call(
        self,
        prompt: str,
        **kwargs: Any,
    ) -> str:
        """Call to Together endpoint."""
        # together.api_key = self.together_api_key
        # output = together.Complete.create(prompt,
        #                                   model=self.model,
        #                                   max_tokens=self.max_tokens,
        #                                   temperature=self.temperature,
        #                                   )
        # text = output['output']['choices'][0]['text']
        # return text
        print(prompt)
        result = client.predict(
				prompt,	# str in 'Question' Textbox component
				0.95,	# int | float (numeric value between 0.05 and 1.0)
				self.temperature,	# int | float (numeric value between 0.1 and 1.0)
				50,	# int | float (numeric value between 1 and 50)
				300,	
				fn_index=0
            )
        return result

In [ ]:

# !wget -O new_papers_2.zip https://www.dropbox.com/scl/fi/67a80h373n1z38088c9fb/new_papers_2.zip?rlkey=1azfz3w5aazd24ihotwzmol2j&dl=1
# !unzip -q new_papers_2.zip -d new_papers

# LangChain multi-doc retriever with ChromaDB

***Key Points***
- Multiple Files - PDFs
- ChromaDB
- LLaMA-2 LLM
- BGE Embeddings


## Setting up LangChain


In [ ]:
import os

In [ ]:
# from langchain.vectorstores import Chroma
from langchain.vectorstores import FAISS
from langchain.text_splitter import RecursiveCharacterTextSplitter

from langchain.chains import RetrievalQA
from langchain.document_loaders import TextLoader
from langchain.document_loaders import PyPDFLoader
from langchain.document_loaders import DirectoryLoader


# from InstructorEmbedding import INSTRUCTOR
# from langchain.embeddings import HuggingFaceInstructEmbeddings

## Load multiple and process documents

In [ ]:
# # Load and process the text files
# # loader = TextLoader('single_text_file.txt')
# loader = DirectoryLoader('votum-ml/pdfs/', glob="./*.pdf", loader_cls=PyPDFLoader)

# documents = loader.load()


import asyncio
import asyncpg




conn = await asyncpg.connect(host="legalscraperserver.postgres.database.azure.com",
            database="postgres",
            user="tejasw",
            password="Password1234",
            port=5432,)
row = await conn.fetch(
        '''SELECT sections, act_name, text
FROM acts
WHERE sections IS NOT NULL''')

# AND(act_name LIKE '%The Indian Penal Code, 1860%' OR act_name LIKE '%The Code of Criminal Procedure, 1973%' OR act_name LIKE '%Motor Vehicles Act%')


In [ ]:
import json
import re


data = []


def remove_between_periods(sentence):
    # Define a regular expression pattern to match text between two periods
    pattern = r'\.(.*?)\.'

    # Use re.sub to replace the matched substring with an empty string
    modified_sentence = re.sub(pattern, '.', sentence)

    return modified_sentence

def preprocess_text(text):
    
    text = text.lower()
    
    # Remove URLs using regex
    text = re.sub(r'http\S+|www\S+|https\S+', '', text)

    # Remove phone numbers (matches formats like +1234567890, 123-456-7890, (123) 456-7890, and more)
    text = re.sub(r'\+?\d{1,4}[-\s]?\(?\d{1,3}\)?[-\s]?\d{1,4}[-\s]?\d{1,4}', '', text)

    # Remove special characters and unwanted sequences (e.g., /xa), except ',' and ':'
    text = re.sub(r'[^a-zA-Z0-9\s,/:\.]|[\xa0]', '', text)
    
    text = text.replace('tweet','')

    # Remove extra whitespace
    text = ' '.join(text.split())

    return text

for act in row:
    for section in act['sections']:
        print(section)
        json_data = json.loads(section)
        if 'omitted.' in json_data['section_name'].lower():
            continue
        json_data['section_name'] = f"{remove_between_periods(json_data['section_name'])} of {act['act_name'].replace(',','')}"
        d = json_data['section_name'] + ' : ' + json_data['text']
        data.append(preprocess_text(d))
 

In [ ]:
len(data)

In [ ]:
#splitting the text into
text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=200)

texts = [text_splitter.split_text(d)[0] for d in data]

len(texts)

In [ ]:
texts[0]

## HF BGE Embeddings

In [ ]:

from langchain.embeddings import HuggingFaceBgeEmbeddings

model_name = "BAAI/bge-base-en"
encode_kwargs = {'normalize_embeddings': True} # set True to compute cosine similarity

model_norm = HuggingFaceBgeEmbeddings(
    model_name=model_name,
    model_kwargs={'device': 'cpu'},
    encode_kwargs=encode_kwargs
)


## create the DB

 T4 GPU

In [ ]:
%%time
# Embed and store the texts
# Supplying a persist_directory will store the embeddings on disk

persist_directory = 'db'

## Here is the nmew embeddings being used
embedding = model_norm

vectordb = FAISS.from_texts(texts,
                                 embedding=embedding)

In [ ]:
# vectordb.save_local("faiss_index")

vectordb = FAISS.load_local('faiss_index',embeddings=model_norm)

## Make a retriever

In [ ]:
retriever = vectordb.as_retriever(search_type='similarity',search_kwargs={"k": 5})

## Make a chain

In [ ]:
import os
import openai

from langchain.chat_models import AzureChatOpenAI
from langchain.schema import HumanMessage



model = AzureChatOpenAI(
    openai_api_base="https://votum.openai.azure.com/",
    openai_api_version= "2023-07-01-preview",
    # openai_api_version="2023-05-15",
    openai_api_key="9ce18c180b8d43cb90568fd0ff6daefd",
    openai_api_type="azure",
    deployment_name='gpt-4'
)

In [ ]:
model(
    [
        HumanMessage(
            content="What model are you?"
        )
    ]
)

In [ ]:
# llm = TogetherLLM(
#     model= "togethercomputer/llama-2-70b-chat",
#     temperature = 0.5,
#     max_tokens = 1024
# )


from langchain.llms import HuggingFaceTextGenInference

llm = HuggingFaceTextGenInference(
    inference_server_url="http://20.83.177.108:8080/",
    max_new_tokens=512,
    top_k=10,
    top_p=0.95,
    typical_p=0.95,
    temperature=0.6,
    # repetition_penalty=1.1,
)


In [ ]:


from langchain.prompts import PromptTemplate


prompt_template = """You are an expert legal assistant with extensive knowledge about Indian law. Your task is to respond to the given query in a consice and factually correct manner. Use the following pieces of context to answer the question at the end. If you don't know the answer, just say that you don't know, don't try to make up an answer.

{context}

Question: {question}
Response:"""


PROMPT = PromptTemplate(
    template=prompt_template, input_variables=["context", "question"]
)

qa_chain = RetrievalQA.from_chain_type(llm=llm,
                                chain_type_kwargs={"prompt": PROMPT},
                                  retriever=retriever,
                                  return_source_documents=True)

In [ ]:
import textwrap

def wrap_text_preserve_newlines(text, width=110):
    # Split the input text into lines based on newline characters
    lines = text.split('\n')

    # Wrap each line individually
    wrapped_lines = [textwrap.fill(line, width=width) for line in lines]

    # Join the wrapped lines back together using newline characters
    wrapped_text = '\n'.join(wrapped_lines)

    return wrapped_text

def process_llm_response(llm_response):
    # print(wrap_text_preserve_newlines(llm_response['result']))
    print(llm_response['result'])
    # print('\n\nSources:')
    # for source in llm_response["source_documents"]:
    #     print(source.metadata['source'])


#, in case you can't find any relevant statutes respond with 'i don't know' rather than providing incorrect answer.
query = """{user_text}"""

    
llm_response = qa_chain(query.format(user_text='How much alcohol can i legally consume before driving'))
print(llm_response)
# process_llm_response(llm_response)

In [ ]:
pip install langchain openai

In [ ]:
from langchain.llms import OpenAI
from langchain.agents import initialize_agent, Tool
from langchain.agents import AgentType
from langchain.agents.react.base import DocstoreExplorer


docstore = DocstoreExplorer(vectordb)
tools = [
    Tool(
        name="Search",
        func=docstore.search,
        description="useful for when you need to ask with search",
    ),
    Tool(
        name="Lookup",
        func=docstore.lookup,
        description="useful for when you need to ask with lookup",
    ),
]

import langchain
langchain.verbose= True
llm = OpenAI(temperature=0)

react = initialize_agent(tools, model, agent=AgentType.REACT_DOCSTORE, verbose=True)

In [ ]:
from langchain.agents import create_pandas_dataframe_agent
from langchain.chat_models import ChatOpenAI
from langchain.agents.agent_types import AgentType
from langchain.tools import tool
import pandas as pd

html = """
<table class="wp-block-table table-layout"><tbody><tr><td><strong>Financial Year</strong></td><td><strong>Cost Inflation Index (CII)</strong></td></tr><tr><td>2001-02 (Base year)</td><td>100</td></tr><tr><td>2002-03</td><td>105</td></tr><tr><td>2003-04</td><td>109</td></tr><tr><td>2004-05</td><td>113</td></tr><tr><td>2005-06</td><td>117</td></tr><tr><td>2006-07</td><td>122</td></tr><tr><td>2007-08</td><td>129</td></tr><tr><td>2008-09</td><td>137</td></tr><tr><td>2009-10</td><td>148</td></tr><tr><td>2010-11</td><td>167</td></tr><tr><td>2011-12</td><td>184</td></tr><tr><td>2012-13</td><td>200</td></tr><tr><td>2013-14</td><td>220</td></tr><tr><td>2014-15</td><td>240</td></tr><tr><td>2015-16</td><td>254</td></tr><tr><td>2016-17</td><td>264</td></tr><tr><td>2017-18</td><td>272</td></tr><tr><td>2018-19</td><td>280</td></tr><tr><td>2019-20</td><td>289</td></tr><tr><td>2020-21</td><td>301</td></tr><tr><td>2021-22</td><td>317</td></tr><tr><td>2022-23</td><td>331</td></tr><tr><td><strong>2023-24</strong></td><td><strong>348</strong></td></tr></tbody></table>
"""

df = pd.read_html(html)[0]


@tool
def read_cii(query: str) -> str:
    """Search for latest indexation value for the given query year."""
    df_agent = create_pandas_dataframe_agent(
        model, df, verbose=True)
    res = df_agent.run(f'what was the indexation in the year {query}')
    return res




In [ ]:
from langchain.llms import OpenAI
from langchain.agents import initialize_agent, Tool
from langchain.agents import AgentType
from langchain.agents import load_tools
import os
from langchain.chat_models import AzureChatOpenAI
from langchain.schema import HumanMessage
import langchain


langchain.verbose = True

model = AzureChatOpenAI(
    openai_api_base="https://votum.openai.azure.com/",
    openai_api_version="2023-07-01-preview",
    # openai_api_version="2023-05-15",
    openai_api_key="9ce18c180b8d43cb90568fd0ff6daefd",
    openai_api_type="azure",
    deployment_name='gpt-4'
)


os.environ["SERPAPI_API_KEY"] = '94de7df75e512ca1fe42b3f51a034a0f0e4683e0f880f9cf7dee1a0eb36a069e'


tools = load_tools(["serpapi", "llm-math"], llm=model)

# ZERO_SHOT_REACT_DESCRIPTION ,CHAT_ZERO_SHOT_REACT_DESCRIPTION
agent_executor = initialize_agent(
    [*tools], model, agent=AgentType.REACT_DOCSTORE, verbose=True)


agent_executor.invoke(
    {"input": "You are an expert Chartered Accountant from India. Answer the following.\nMr X bought equity shares on 15th Dec, 2016 for Rs. 10,000. FMV of the shares was Rs. 12,000 as on 31st Jan, 18. He sold the shares on 10th May, 2018 for Rs. 15,000. What will be the long-term capital gain or loss?"})


In [ ]:
agent_executor = initialize_agent(tools, llm, agent=AgentType.REACT_DOCSTORE, verbose=True)
agent_executor.invoke({"input": "What is the punishment for drinking and driving?"})

In [ ]:
together.Models.stop("togethercomputer/llama-2-70b-chat")

In [ ]:
import re

import numpy as np

from langchain.schema import BaseRetriever
from langchain.callbacks.manager import (
    AsyncCallbackManagerForRetrieverRun,
    CallbackManagerForRetrieverRun,
)
from langchain.utilities import GoogleSerperAPIWrapper
from langchain.schema import Document
from typing import Any, List





class SerperSearchRetriever(BaseRetriever):
    search: GoogleSerperAPIWrapper = None

    def _get_relevant_documents(
        self, query: str, *, run_manager: CallbackManagerForRetrieverRun, **kwargs: Any
    ) -> List[Document]:
        return [Document(page_content=self.search.run(query))]

    async def _aget_relevant_documents(
        self,
        query: str,
        *,
        run_manager: AsyncCallbackManagerForRetrieverRun,
        **kwargs: Any,
    ) -> List[Document]:
        raise NotImplementedError()


retriever = SerperSearchRetriever(search=GoogleSerperAPIWrapper())


In [ ]:
# We set this so we can see what exactly is going on
from langchain.chains import FlareChain
import langchain

langchain.verbose = True

os.environ['OPENAI_API_KEY'] = 'wd'


flare = FlareChain.from_llm(
    llm=model,
    retriever=retriever,
    max_generation_len=164,
    min_prob=0.3,
)


query = "explain in great detail the difference between the langchain framework and baby agi"
flare.run(query)


In [ ]:
os.environ["SERPER_API_KEY"] = '94de7df75e512ca1fe42b3f51a034a0f0e4683e0f880f9cf7dee1a0eb36a069e'

In [ ]:
from langchain.chat_models import ChatOpenAI
import openai
from langchain.adapters import openai as lc_openai
import os

from langchain.agents import initialize_agent, Tool
from langchain.agents import AgentType
from langchain.agents import load_tools

openai.api_base = "http://20.83.177.108:8080/v1"
openai.api_key = "none"



# create a request activating streaming response
# for chunk in openai.ChatCompletion.create(
#     model="Qwen",
#     messages=[
#         {"role": "user", "content": "Hi"}
#     ],
#     stream=True
#     # Specifying stop words in streaming output format is not yet supported and is under development.
# ):
#     if hasattr(chunk.choices[0].delta, "content"):
#         print(chunk.choices[0].delta.content, end="", flush=True)


# response = openai.ChatCompletion.create(
    # openai_api_base='http://20.83.177.108:8080/v1',
    # openai_api_key='none',
#     model="Qwen",
#     messages=[
#         {"role": "user", "content": "Hi"}
#     ],
#     stream=False,
#     # You can add custom stop words here, e.g., stop=["Observation:"] for ReAct prompting.
#     stop=[]
# )
# print(response.choices[0].message.content)


os.environ["SERPAPI_API_KEY"] = '94de7df75e512ca1fe42b3f51a034a0f0e4683e0f880f9cf7dee1a0eb36a069e'
llm = ChatOpenAI(openai_api_base='http://20.83.177.108:8080/v1',
                 openai_api_key='none',)

tools = load_tools(["serpapi", "llm-math"], llm=llm)

agent_executor = initialize_agent(
    [*tools], llm, agent=AgentType.ZERO_SHOT_REACT_DESCRIPTION, verbose=True)


agent_executor.invoke(
    {"input": "?"})





In [ ]:
from langchain.chat_models import ChatOpenAI
from langchain_experimental.plan_and_execute import PlanAndExecute, load_agent_executor, load_chat_planner
from langchain.llms import OpenAI
from langchain.utilities import SerpAPIWrapper
from langchain.agents.tools import Tool
from langchain.chains import LLMMathChain
from langchain.agents import load_tools

import os

os.environ["SERPAPI_API_KEY"] = '94de7df75e512ca1fe42b3f51a034a0f0e4683e0f880f9cf7dee1a0eb36a069e'
tools = load_tools(["serpapi", "llm-math"], llm=model)
planner = load_chat_planner(model)
executor = load_agent_executor(model, tools, verbose=True)
plan_agent = PlanAndExecute(planner=planner, executor=executor, verbose=True)


plan_agent.run(
    'Plan a 5 day trip for me to Paris, My budget is $2000. I would prefer 4 star hotel and minimal traveling. I live in Delhi, India,')
